<a href="https://cognitiveclass.ai"><img src = "https://ibm.box.com/shared/static/9gegpsmnsoo25ikkbl4qzlvlyjbgxs5x.png" width = 400> </a>

<h1 align=center><font size = 5>Segmenting and Clustering Neighborhoods in Toronto</font></h1>

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')



Solving environment: done

# All requested packages already installed.

Solving environment: done

# All requested packages already installed.

Libraries imported.


 <font size="3"> __Lets scrape the boroughs and neighbourhoods from wikipedia using BeautifulSoup__ </font>

In [2]:

from bs4 import BeautifulSoup
import requests

r  = requests.get("https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M")

wiki_html = r.text

soup = BeautifulSoup(wiki_html)
print(soup.prettify())

<!DOCTYPE html>
<html class="client-nojs" dir="ltr" lang="en">
 <head>
  <meta charset="utf-8"/>
  <title>
   List of postal codes of Canada: M - Wikipedia
  </title>
  <script>
   document.documentElement.className="client-js";RLCONF={"wgBreakFrames":!1,"wgSeparatorTransformTable":["",""],"wgDigitTransformTable":["",""],"wgDefaultDateFormat":"dmy","wgMonthNames":["","January","February","March","April","May","June","July","August","September","October","November","December"],"wgMonthNamesShort":["","Jan","Feb","Mar","Apr","May","Jun","Jul","Aug","Sep","Oct","Nov","Dec"],"wgRequestId":"Xg1lcwpAICgAALHCp4UAAADQ","wgCSPNonce":!1,"wgCanonicalNamespace":"","wgCanonicalSpecialPageName":!1,"wgNamespaceNumber":0,"wgPageName":"List_of_postal_codes_of_Canada:_M","wgTitle":"List of postal codes of Canada: M","wgCurRevisionId":933624196,"wgRevisionId":933624196,"wgArticleId":539066,"wgIsArticle":!0,"wgIsRedirect":!1,"wgAction":"view","wgUserName":null,"wgUserGroups":["*"],"wgCategories":["Communi

 <font size="3"> __Let's extract the data from the right table__ </font>

In [3]:
table = soup.find('table', attrs={'class':'wikitable sortable'})
table_rows = table.find_all('tr')
l = []
for tr in table_rows:
    td = tr.find_all('td')
    row = [tr.text for tr in td]
    l.append(row)
df  = pd.DataFrame(l, columns=["PostalCode", "Borough", "Neighborhood"])
df.head()

PostalCode       Borough        Neighborhood
0       None          None                None
1        M1A  Not assigned      Not assigned\n
2        M2A  Not assigned      Not assigned\n
3        M3A    North York         Parkwoods\n
4        M4A    North York  Victoria Village\n

 <font size="3"> __Let's get rid of the newline characters__ </font>

In [4]:

df['Neighborhood'] = df['Neighborhood'].str.replace("\n", "")


 <font size="3"> __Let's remove 'Not assigned' values__ </font>

In [5]:
df = df.astype(str)
df = df[ (df.Borough != 'Not assigned')  ]
df.head()

PostalCode           Borough      Neighborhood
0       None              None              None
3        M3A        North York         Parkwoods
4        M4A        North York  Victoria Village
5        M5A  Downtown Toronto      Harbourfront
6        M6A        North York  Lawrence Heights

In [6]:
df = df.sort_values(by=['PostalCode'])
df.head()

PostalCode      Borough    Neighborhood
12        M1B  Scarborough         Malvern
11        M1B  Scarborough           Rouge
27        M1C  Scarborough  Highland Creek
29        M1C  Scarborough      Port Union
28        M1C  Scarborough      Rouge Hill

In [7]:
df[ df.Neighborhood == 'Not assigned'] 

PostalCode       Borough  Neighborhood
10        M9A  Queen's Park  Not assigned

 <font size="3"> __Let's set missing neighbourhoods to the borough__ </font>

In [8]:
df['Neighborhood'] = np.where(df['Neighborhood'] == 'Not assigned', df['Borough'], df['Neighborhood'])
df[ df.PostalCode == 'M7A'] 

PostalCode           Borough  Neighborhood
8        M7A  Downtown Toronto  Queen's Park

 <font size="3"> __Let's group by postal code concatenating the neighbourhoods__ </font>

In [9]:
df = df.groupby(['PostalCode','Borough'])['Neighborhood'].apply(', '.join).reset_index()
df.head()

PostalCode      Borough                            Neighborhood
0        M1B  Scarborough                          Malvern, Rouge
1        M1C  Scarborough  Highland Creek, Port Union, Rouge Hill
2        M1E  Scarborough       West Hill, Morningside, Guildwood
3        M1G  Scarborough                                  Woburn
4        M1H  Scarborough                               Cedarbrae

 <font size="3"> __Here is the wanted shape of the data frame__ </font>

In [10]:
df.shape

(104, 3)

 <font size="3"> __Loading and merging the latitude and longitude data__ </font>

In [11]:
toronto_geo_df = pd.read_csv('Geospatial_Coordinates.csv')
toronto_geo_df = toronto_geo_df.rename(columns={'Postal Code': 'PostalCode'})
toronto_geo_df.head()

PostalCode   Latitude  Longitude
0        M1B  43.806686 -79.194353
1        M1C  43.784535 -79.160497
2        M1E  43.763573 -79.188711
3        M1G  43.770992 -79.216917
4        M1H  43.773136 -79.239476

In [12]:
df = pd.merge(df, toronto_geo_df, on= 'PostalCode')
df.head()

PostalCode      Borough                            Neighborhood   Latitude  \
0        M1B  Scarborough                          Malvern, Rouge  43.806686   
1        M1C  Scarborough  Highland Creek, Port Union, Rouge Hill  43.784535   
2        M1E  Scarborough       West Hill, Morningside, Guildwood  43.763573   
3        M1G  Scarborough                                  Woburn  43.770992   
4        M1H  Scarborough                               Cedarbrae  43.773136   

   Longitude  
0 -79.194353  
1 -79.160497  
2 -79.188711  
3 -79.216917  
4 -79.239476

### lets only explore neighborhoods of boroughs with Toronto in it
 

In [13]:
neighborhoods = df[df['Borough'].str.contains("Toronto")].reset_index(drop=True)
neighborhoods.head()


PostalCode          Borough                    Neighborhood   Latitude  \
0        M4E     East Toronto                     The Beaches  43.676357   
1        M4K     East Toronto    The Danforth West, Riverdale  43.679557   
2        M4L     East Toronto  India Bazaar, The Beaches West  43.668999   
3        M4M     East Toronto                 Studio District  43.659526   
4        M4N  Central Toronto                   Lawrence Park  43.728020   

   Longitude  
0 -79.293031  
1 -79.352188  
2 -79.315572  
3 -79.340923  
4 -79.388790

#### Use geopy library to get the latitude and longitude values of Toronto.

In order to define an instance of the geocoder, we need to define a user_agent. We will name our agent <em>t_explorer</em>, as shown below.

In [14]:
address = 'Toronto, Ontario'

geolocator = Nominatim(user_agent="t_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto are 43.653963, -79.387207.


#### Create a map of Toronto with neighborhoods superimposed on top.

In [15]:
# create map of Toronto using latitude and longitude values
map_toronto= folium.Map(location=[latitude, longitude], zoom_start=12)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

**Folium** is a great visualization library. Feel free to zoom into the above map, and click on each circle mark to reveal the name of the neighborhood and its respective borough.

Next, we are going to start utilizing the Foursquare API to explore the neighborhoods and segment them.

#### Define Foursquare Credentials and Version

In [50]:
CLIENT_ID = 'XXX' # your Foursquare ID
CLIENT_SECRET = 'XXX' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: XXX
CLIENT_SECRET:XXX


Get the neighborhood's name.

In [17]:
neighborhoods.loc[0, 'Neighborhood']

'The Beaches'

Get the neighborhood's latitude and longitude values.

In [18]:
neighborhood_latitude = neighborhoods.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = neighborhoods.loc[0, 'Longitude'] # neighborhood longitude value

neighborhood_name = neighborhoods.loc[0, 'Neighborhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of The Beaches are 43.6763574, -79.2930312.


#### Now, let's get the top 100 venues that are in "The Beaches" within a radius of 500 meters.

First, let's create the GET request URL. Name your URL **url**.

In [51]:
# type your answer here

LIMIT = 100 # limit of number of venues returned by Foursquare API

radius = 500 # define radius

# create URL
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
url # display URL



'https://api.foursquare.com/v2/venues/explore?&client_id=XXX&client_secret=XXX&v=20180605&ll=43.6763574,-79.2930312&radius=500&limit=100'

Send the GET request and examine the resutls

In [20]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5e0fa0597828ae001b51533c'},
 'response': {'headerLocation': 'The Beaches',
  'headerFullLocation': 'The Beaches, Toronto',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 4,
  'suggestedBounds': {'ne': {'lat': 43.6808574045, 'lng': -79.28682091449052},
   'sw': {'lat': 43.6718573955, 'lng': -79.29924148550948}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4bd461bc77b29c74a07d9282',
       'name': 'Glen Manor Ravine',
       'location': {'address': 'Glen Manor',
        'crossStreet': 'Queen St.',
        'lat': 43.67682094413784,
        'lng': -79.29394208780985,
        'labeledLatLngs': [{'label': 'display',
          'lat': 43.67682094413784,
          'lng': -79.29394208780985}],
        'distance': 89,
     

From the Foursquare lab in the previous module, we know that all the information is in the *items* key. Before we proceed, let's borrow the **get_category_type** function from the Foursquare lab.

In [21]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

Now we are ready to clean the json and structure it into a *pandas* dataframe.

In [22]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues

name         categories        lat        lng
0                   Glen Manor Ravine              Trail  43.676821 -79.293942
1  The Big Carrot Natural Food Market  Health Food Store  43.678879 -79.297734
2                 Grover Pub and Grub                Pub  43.679181 -79.297215
3                       Upper Beaches       Neighborhood  43.680563 -79.292869

And how many venues were returned by Foursquare?

In [23]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

4 venues were returned by Foursquare.


<a id='item2'></a>

## 2. Explore Neighborhoods in Toronto

#### Let's create a function to repeat the same process to all the neighborhoods in Toronto

In [24]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

#### Now write the code to run the above function on each neighborhood and create a new dataframe called *toronto_venues*.

In [25]:

df2 = df.copy()
df2.Neighborhood = df2.Neighborhood.str.split(",")

#df.Neighborhood.apply(pd.Series)
df2 = df2.explode('Neighborhood')


In [26]:
df2

PostalCode           Borough  \
0          M1B       Scarborough   
0          M1B       Scarborough   
1          M1C       Scarborough   
1          M1C       Scarborough   
1          M1C       Scarborough   
2          M1E       Scarborough   
2          M1E       Scarborough   
2          M1E       Scarborough   
3          M1G       Scarborough   
4          M1H       Scarborough   
5          M1J       Scarborough   
6          M1K       Scarborough   
6          M1K       Scarborough   
6          M1K       Scarborough   
7          M1L       Scarborough   
7          M1L       Scarborough   
7          M1L       Scarborough   
8          M1M       Scarborough   
8          M1M       Scarborough   
8          M1M       Scarborough   
9          M1N       Scarborough   
9          M1N       Scarborough   
10         M1P       Scarborough   
10         M1P       Scarborough   
10         M1P       Scarborough   
11         M1R       Scarborough   
11         M1R       Scarborough   
12         M1S       Scarborough   
13         M1T       Scarborough   
13         M1T       Scarborough   
13         M1T       Scarborough   
14         M1V       Scarborough   
14         M1V       Scarborough   
14         M1V       Scarborough   
14         M1V       Scarborough   
15         M1W       Scarborough   
16         M1X       Scarborough   
17         M2H        North York   
18         M2J        North York   
18         M2J        North York   
18         M2J        North York   
19         M2K        North York   
20         M2L        North York   
20         M2L        North York   
21         M2M        North York   
21         M2M        North York   
22         M2N        North York   
23         M2P        North York   
24         M2R        North York   
25         M3A        North York   
26         M3B        North York   
27         M3C        North York   
27         M3C        North York   
28         M3H        North York   
28         M3H        North York   
28         M3H        North York   
29         M3J        North York   
29         M3J        North York   
30         M3K        North York   
30         M3K        North York   
31         M3L        North York   
32         M3M        North York   
33         M3N        North York   
34         M4A        North York   
35         M4B         East York   
35         M4B         East York   
36         M4C         East York   
37         M4E      East Toronto   
38         M4G         East York   
39         M4H         East York   
40         M4J         East York   
41         M4K      East Toronto   
41         M4K      East Toronto   
42         M4L      East Toronto   
42         M4L      East Toronto   
43         M4M      East Toronto   
44         M4N   Central Toronto   
45         M4P   Central Toronto   
46         M4R   Central Toronto   
47         M4S   Central Toronto   
48         M4T   Central Toronto   
48         M4T   Central Toronto   
49         M4V   Central Toronto   
49         M4V   Central Toronto   
49         M4V   Central Toronto   
49         M4V   Central Toronto   
49         M4V   Central Toronto   
50         M4W  Downtown Toronto   
51         M4X  Downtown Toronto   
51         M4X  Downtown Toronto   
52         M4Y  Downtown Toronto   
53         M5A  Downtown Toronto   
54         M5B  Downtown Toronto   
54         M5B  Downtown Toronto   
55         M5C  Downtown Toronto   
56         M5E  Downtown Toronto   
57         M5G  Downtown Toronto   
58         M5H  Downtown Toronto   
58         M5H  Downtown Toronto   
58         M5H  Downtown Toronto   
59         M5J  Downtown Toronto   
59         M5J  Downtown Toronto   
59         M5J  Downtown Toronto   
60         M5K  Downtown Toronto   
60         M5K  Downtown Toronto   
61         M5L  Downtown Toronto   
61         M5L  Downtown Toronto   
62         M5M        North York   
62         M5M        North York   
63         M5N   Central Toronto   
64      

In [28]:

toronto_venues = getNearbyVenues(names=df2['Neighborhood'],
                                   latitudes=df2['Latitude'],
                                   longitudes=df2['Longitude']
                                  )



Malvern
 Rouge
Highland Creek
 Port Union
 Rouge Hill
West Hill
 Morningside
 Guildwood
Woburn
Cedarbrae
Scarborough Village
East Birchmount Park
 Kennedy Park
 Ionview
Oakridge
 Clairlea
 Golden Mile
Cliffside
 Cliffcrest
 Scarborough Village West
Cliffside West
 Birch Cliff
Scarborough Town Centre
 Wexford Heights
 Dorset Park
Maryvale
 Wexford
Agincourt
Sullivan
 Tam O'Shanter
 Clarks Corners
Milliken
 Steeles East
 L'Amoreaux East
 Agincourt North
L'Amoreaux West
Upper Rouge
Hillcrest Village
Fairview
 Henry Farm
 Oriole
Bayview Village
York Mills
 Silver Hills
Newtonbrook
 Willowdale
Willowdale South
York Mills West
Willowdale West
Parkwoods
Don Mills North
Don Mills South
 Flemingdon Park
Bathurst Manor
 Downsview North
 Wilson Heights
York University
 Northwood Park
CFB Toronto
 Downsview East
Downsview West
Downsview Central
Downsview Northwest
Victoria Village
Woodbine Gardens
 Parkview Hill
Woodbine Heights
The Beaches
Leaside
Thorncliffe Park
East Toronto
The Danforth West
 

#### Let's check the size of the resulting dataframe

In [29]:
print(toronto_venues.shape)
toronto_venues


(4331, 7)


Neighborhood  \
0                                               Malvern   
1                                               Malvern   
2                                                 Rouge   
3                                                 Rouge   
4                                        Highland Creek   
5                                        Highland Creek   
6                                            Port Union   
7                                            Port Union   
8                                            Rouge Hill   
9                                            Rouge Hill   
10                                            West Hill   
11                                            West Hill   
12                                            West Hill   
13                                            West Hill   
14                                            West Hill   
15                                            West Hill   
16                                            West Hill   
17                                          Morningside   
18                                          Morningside   
19                                          Morningside   
20                                          Morningside   
21                                          Morningside   
22                                          Morningside   
23                                          Morningside   
24                                            Guildwood   
25                                            Guildwood   
26                                            Guildwood   
27                                            Guildwood   
28                                            Guildwood   
29                                            Guildwood   
30                                            Guildwood   
31                                               Woburn   
32                                               Woburn   
33                                               Woburn   
34                                               Woburn   
35                                            Cedarbrae   
36                                            Cedarbrae   
37                                            Cedarbrae   
38                                            Cedarbrae   
39                                            Cedarbrae   
40                                            Cedarbrae   
41                                            Cedarbrae   
42                                            Cedarbrae   
43                                  Scarborough Village   
44                                  Scarborough Village   
45                                 East Birchmount Park   
46                                 East Birchmount Park   
47                                 East Birchmount Park   
48                                 East Birchmount Park   
49                                 East Birchmount Park   
50                                 East Birchmount Park   
51                                 East Birchmount Park   
52                                         Kennedy Park   
53                                         Kennedy Park   
54                                         Kennedy Park   
55                                         Kennedy Park   
56                                         Kennedy Park   
57                                         Kennedy Park   
58                                         Kennedy Park   
59                                              Ionview   
60                                              Ionview   
61                                              Ionview   
62                                              Ionview   
63                                              Ionview   
64                                              Ionview   
65                                              Ionview   
66                                             Oakridge   
67                             

Let's check how many venues were returned for each neighborhood

In [30]:
toronto_venues.groupby('Neighborhood').size().reset_index(name ='counts')

Neighborhood  counts
0                                      Agincourt North       4
1                                       Albion Gardens       9
2                                        Bathurst Quay      16
3                                     Beaumond Heights       9
4                                         Bedford Park      22
5                                          Birch Cliff       4
6                                    Bloordale Gardens       7
7                                             CN Tower      16
8                                             Clairlea       9
9                                       Clarks Corners      11
10                                          Cliffcrest       3
11                                           Deer Park      16
12                                         Dorset Park       6
13                                  Dovercourt Village      17
14                                      Downsview East       2
15                                     Downsview North      20
16                                            Eringate       7
17                                    Exhibition Place      21
18                                First Canadian Place     100
19                                     Flemingdon Park      22
20                                   Forest Hill North       4
21                                      Forest Hill SE      16
22                                     Garden District     100
23                                         Golden Mile       9
24                                         Grange Park      90
25                                           Guildwood       7
26                                             Harbord      38
27                                   Harbourfront East     100
28                                          Henry Farm      62
29                                          Humber Bay       1
30                                   Humber Bay Shores      13
31                                          Humbergate       9
32                                           Humberlea       1
33                                             Ionview       7
34                                      Island airport      16
35                                           Islington       1
36                                           Jamestown       9
37                                          Keelesdale       5
38                                        Kennedy Park       7
39                                   Kensington Market      90
40                                                King     100
41                                    King and Spadina      16
42                                    King's Mill Park       1
43                            Kingsway Park South East       1
44                            Kingsway Park South West      14
45                                     L'Amoreaux East       4
46                                    Lawrence Heights       8
47                                         Long Branch      10
48                                        Martin Grove       1
49                                Martin Grove Gardens       4
50                                           Mimico NE       1
51                                        Mimico South      13
52                                     Montgomery Road       3
53                                          Moore Park       4
54                                         Morningside       7
55                                        Mount Dennis       5
56                                         Mount Olive       9
57                                          North Park       5
58                                      Northwood Park       5
59                                   Old Burnhamthorpe       7
60                                      Old Mill North       3
61                                      Old Mill South       1
62                                              Oriole      62
63        

#### Let's find out how many unique categories can be curated from all the returned venues

In [31]:
print('There are {} uniques categories.'.format(len(toronto_venues['Venue Category'].unique())))

There are 273 uniques categories.


<a id='item3'></a>

## 3. Analyze Each Neighborhood

In [32]:
# one hot encoding
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighborhood'] = toronto_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.head()

Yoga Studio  Accessories Store  Afghan Restaurant  Airport  \
0            0                  0                  0        0   
1            0                  0                  0        0   
2            0                  0                  0        0   
3            0                  0                  0        0   
4            0                  0                  0        0   

   Airport Food Court  Airport Gate  Airport Lounge  Airport Service  \
0                   0             0               0                0   
1                   0             0               0                0   
2                   0             0               0                0   
3                   0             0               0                0   
4                   0             0               0                0   

   Airport Terminal  American Restaurant  Antique Shop  Aquarium  Art Gallery  \
0                 0                    0             0         0            0   
1                 0                    0             0         0            0   
2                 0                    0             0         0            0   
3                 0                    0             0         0            0   
4                 0                    0             0         0            0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Auto Workshop  \
0                    0                 0                   0              0   
1                    0                 0                   0              0   
2                    0                 0                   0              0   
3                    0                 0                   0              0   
4                    0                 0                   0              0   

   BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  Baseball Field  \
0          0           0           0       0     0    0               0   
1          0           0           0       0     0    0               0   
2          0           0           0       0     0    0               0   
3          0           0           0       0     0    0               0   
4          0           0           0       0     0    0               0   

   Baseball Stadium  Basketball Court  Basketball Stadium  Beach  \
0                 0                 0                   0      0   
1                 0                 0                   0      0   
2                 0                 0                   0      0   
3                 0                 0                   0      0   
4                 0                 0                   0      0   

   Bed & Breakfast  Beer Bar  Beer Store  Belgian Restaurant  Bike Shop  \
0                0         0           0                   0          0   
1                0         0           0                   0          0   
2                0         0           0                   0          0   
3                0         0           0                   0          0   
4                0         0           0                   0          0   

   Bistro  Board Shop  Boat or Ferry  Bookstore  Boutique  Bowling Alley  \
0       0           0              0          0         0              0   
1       0           0              0          0         0              0   
2       0           0              0          0         0              0   
3       0           0              0          0         0              0   
4       0           0              0          0         0              0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  \
0                     0               0        0            0   
1                     0               0        0            0   
2                     0               0        0            0   
3                     0               0        0            0   
4                     0               0        0            0   

   Bubble Tea Shop  Building  Burger Joint  Burrito Place 

And let's examine the new dataframe size.

In [33]:
toronto_onehot.shape

(4331, 273)

#### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [34]:
toronto_grouped = toronto_onehot.groupby('Neighborhood').mean().reset_index()
toronto_grouped

Neighborhood  Yoga Studio  \
0                                      Agincourt North     0.000000   
1                                       Albion Gardens     0.000000   
2                                        Bathurst Quay     0.000000   
3                                     Beaumond Heights     0.000000   
4                                         Bedford Park     0.000000   
5                                          Birch Cliff     0.000000   
6                                    Bloordale Gardens     0.000000   
7                                             CN Tower     0.000000   
8                                             Clairlea     0.000000   
9                                       Clarks Corners     0.000000   
10                                          Cliffcrest     0.000000   
11                                           Deer Park     0.000000   
12                                         Dorset Park     0.000000   
13                                  Dovercourt Village     0.000000   
14                                      Downsview East     0.000000   
15                                     Downsview North     0.000000   
16                                            Eringate     0.000000   
17                                    Exhibition Place     0.000000   
18                                First Canadian Place     0.000000   
19                                     Flemingdon Park     0.000000   
20                                   Forest Hill North     0.000000   
21                                      Forest Hill SE     0.000000   
22                                     Garden District     0.000000   
23                                         Golden Mile     0.000000   
24                                         Grange Park     0.000000   
25                                           Guildwood     0.000000   
26                                             Harbord     0.026316   
27                                   Harbourfront East     0.000000   
28                                          Henry Farm     0.000000   
29                                          Humber Bay     0.000000   
30                                   Humber Bay Shores     0.000000   
31                                          Humbergate     0.000000   
32                                           Humberlea     0.000000   
33                                             Ionview     0.000000   
34                                      Island airport     0.000000   
35                                           Islington     0.000000   
36                                           Jamestown     0.000000   
37                                          Keelesdale     0.000000   
38                                        Kennedy Park     0.000000   
39                                   Kensington Market     0.000000   
40                                                King     0.000000   
41                                    King and Spadina     0.000000   
42                                    King's Mill Park     0.000000   
43                            Kingsway Park South East     0.000000   
44                            Kingsway Park South West     0.000000   
45                                     L'Amoreaux East     0.000000   
46                                    Lawrence Heights     0.000000   
47                                         Long Branch     0.000000   
48                                        Martin Grove     0.000000   
49                                Martin Grove Gardens     0.000000   
50                                           Mimico NE     0.000000   
51                                        Mimico South     0.000000   
52                                     Montgomery Road     0.000000   
53                                          Moore Park     0.000000   
54                                         Morningside     0.000000   
55                                        Mount Dennis     0.00000

#### Let's confirm the new size

In [35]:
toronto_grouped.shape

(206, 273)

#### Let's print each neighborhood along with the top 5 most common venues

In [36]:
num_top_venues = 5

for hood in toronto_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = toronto_grouped[toronto_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

---- Agincourt North----
                 venue  freq
0           Playground  0.25
1                 Park  0.25
2          Coffee Shop  0.25
3  Arts & Crafts Store  0.25
4   Mexican Restaurant  0.00


---- Albion Gardens----
                  venue  freq
0         Grocery Store  0.22
1           Pizza Place  0.11
2           Video Store  0.11
3        Sandwich Place  0.11
4  Fast Food Restaurant  0.11


---- Bathurst Quay----
             venue  freq
0  Airport Service  0.19
1         Boutique  0.06
2  Harbor / Marina  0.06
3              Bar  0.06
4      Coffee Shop  0.06


---- Beaumond Heights----
                  venue  freq
0         Grocery Store  0.22
1           Pizza Place  0.11
2           Video Store  0.11
3        Sandwich Place  0.11
4  Fast Food Restaurant  0.11


---- Bedford Park----
                  venue  freq
0  Fast Food Restaurant  0.09
1           Coffee Shop  0.09
2    Italian Restaurant  0.09
3      Sushi Restaurant  0.05
4            Restaurant  0.05


---- B

                             venue  freq
0                   Baseball Field   1.0
1                      Yoga Studio   0.0
2               Mexican Restaurant   0.0
3  Molecular Gastronomy Restaurant   0.0
4       Modern European Restaurant   0.0


---- Kingsway Park South East----
                             venue  freq
0                   Baseball Field   1.0
1                      Yoga Studio   0.0
2               Mexican Restaurant   0.0
3  Molecular Gastronomy Restaurant   0.0
4       Modern European Restaurant   0.0


---- Kingsway Park South West----
            venue  freq
0     Social Club  0.07
1   Tanning Salon  0.07
2  Discount Store  0.07
3  Sandwich Place  0.07
4   Burrito Place  0.07


---- L'Amoreaux East----
                 venue  freq
0           Playground  0.25
1                 Park  0.25
2          Coffee Shop  0.25
3  Arts & Crafts Store  0.25
4   Mexican Restaurant  0.00


---- Lawrence Heights----
                    venue  freq
0  Furniture / Home Store  0.25

                venue  freq
0         Coffee Shop  0.07
1                Park  0.05
2          Restaurant  0.05
3              Bakery  0.05
4  Italian Restaurant  0.05


---- St. Phillips----
                venue  freq
0         Pizza Place  0.25
1                Park  0.25
2            Bus Line  0.25
3   Mobile Phone Shop  0.25
4  Mexican Restaurant  0.00


---- Steeles East----
                 venue  freq
0           Playground  0.25
1                 Park  0.25
2          Coffee Shop  0.25
3  Arts & Crafts Store  0.25
4   Mexican Restaurant  0.00


---- Summerhill West----
                venue  freq
0  Light Rail Station  0.12
1         Coffee Shop  0.12
2                 Pub  0.12
3        Liquor Store  0.06
4          Sports Bar  0.06


---- Sunnylea----
                             venue  freq
0                   Baseball Field   1.0
1                      Yoga Studio   0.0
2               Mexican Restaurant   0.0
3  Molecular Gastronomy Restaurant   0.0
4       Modern Europea

                   venue  freq
0   Fast Food Restaurant   0.4
1         Sandwich Place   0.2
2             Restaurant   0.2
3  Check Cashing Service   0.2
4    Monument / Landmark   0.0


----Design Exchange----
                 venue  freq
0          Coffee Shop  0.13
1                Hotel  0.07
2                 Café  0.06
3           Restaurant  0.04
4  American Restaurant  0.03


----Don Mills North----
                  venue  freq
0  Caribbean Restaurant   0.2
1  Gym / Fitness Center   0.2
2   Japanese Restaurant   0.2
3      Basketball Court   0.2
4                  Café   0.2


----Don Mills South----
              venue  freq
0       Coffee Shop  0.09
1  Asian Restaurant  0.09
2        Beer Store  0.09
3               Gym  0.09
4    Sandwich Place  0.05


----Downsview----
                        venue  freq
0  Construction & Landscaping   0.2
1                        Park   0.2
2            Basketball Court   0.2
3               Deli / Bodega   0.2
4                      Bak

                        venue  freq
0                        Park  0.50
1                       Trail  0.25
2                  Playground  0.25
3                 Yoga Studio  0.00
4  Modern European Restaurant  0.00


----Roselawn----
                             venue  freq
0                           Garden   0.5
1                     Home Service   0.5
2               Mexican Restaurant   0.0
3              Monument / Landmark   0.0
4  Molecular Gastronomy Restaurant   0.0


----Royal York South East----
                             venue  freq
0                   Baseball Field   1.0
1                      Yoga Studio   0.0
2               Mexican Restaurant   0.0
3  Molecular Gastronomy Restaurant   0.0
4       Modern European Restaurant   0.0


----Runnymede----
                  venue  freq
0  Caribbean Restaurant  0.25
1               Brewery  0.25
2         Grocery Store  0.25
3              Bus Line  0.25
4           Yoga Studio  0.00


----Ryerson----
                       

#### Let's put that into a *pandas* dataframe

First, let's write a function to sort the venues in descending order.

In [37]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories = row_categories[row_categories > 0]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    nan_padding = pd.Series([np.nan])
    nan_padding = nan_padding.repeat([10])
    
    row_categories_sorted = row_categories_sorted.append(nan_padding)
        
    return row_categories_sorted.index.values[0:num_top_venues]

Now let's create the new dataframe and display the top 10 venues for each neighborhood.

In [38]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = toronto_grouped['Neighborhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0    Agincourt North            Playground                  Park   
1     Albion Gardens         Grocery Store           Video Store   
2      Bathurst Quay       Airport Service      Sculpture Garden   
3   Beaumond Heights         Grocery Store           Video Store   
4       Bedford Park    Italian Restaurant           Coffee Shop   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0           Coffee Shop   Arts & Crafts Store                     0   
1        Sandwich Place           Pizza Place              Pharmacy   
2   Rental Car Location                 Plane       Harbor / Marina   
3        Sandwich Place           Pizza Place              Pharmacy   
4  Fast Food Restaurant     Indian Restaurant               Butcher   

  6th Most Common Venue    7th Most Common Venue 8th Most Common Venue  \
0                     0                        0                     0   
1   Fried Chicken Joint     Fast Food Restaurant            Beer Store   
2           Coffee Shop                 Boutique         Boat or Ferry   
3   Fried Chicken Joint     Fast Food Restaurant            Beer Store   
4                  Café  Comfort Food Restaurant      Greek Restaurant   

  9th Most Common Venue 10th Most Common Venue  
0                     0                      0  
1                     0                      0  
2                   Bar       Airport Terminal  
3                     0                      0  
4         Grocery Store        Thai Restaurant

In [39]:
row = toronto_grouped.iloc[1, :]
#row
    
#remove neioghbourhood
row_categories = row.iloc[1:]
row_categories = row_categories[row_categories > 0]
row_categories
row_categories_sorted = row_categories.sort_values(ascending=False)
#remove 0 
    
row_categories_sorted.index.values[0:10]

array(['Grocery Store', 'Video Store', 'Sandwich Place', 'Pizza Place',
       'Pharmacy', 'Fried Chicken Joint', 'Fast Food Restaurant',
       'Beer Store'], dtype=object)

<a id='item4'></a>

## 4. Cluster Neighborhoods

Run *k*-means to cluster the neighborhood into 5 clusters.

In [40]:
# set number of clusters
kclusters = 5

toronto_grouped_clustering = toronto_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([0, 1, 1, 1, 1, 1, 1, 1, 1, 1])

Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [41]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)


In [42]:
toronto_merged = df2.copy()

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
toronto_merged = toronto_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

toronto_merged # check the last columns!''

PostalCode           Borough  \
0          M1B       Scarborough   
0          M1B       Scarborough   
1          M1C       Scarborough   
1          M1C       Scarborough   
1          M1C       Scarborough   
2          M1E       Scarborough   
2          M1E       Scarborough   
2          M1E       Scarborough   
3          M1G       Scarborough   
4          M1H       Scarborough   
5          M1J       Scarborough   
6          M1K       Scarborough   
6          M1K       Scarborough   
6          M1K       Scarborough   
7          M1L       Scarborough   
7          M1L       Scarborough   
7          M1L       Scarborough   
8          M1M       Scarborough   
8          M1M       Scarborough   
8          M1M       Scarborough   
9          M1N       Scarborough   
9          M1N       Scarborough   
10         M1P       Scarborough   
10         M1P       Scarborough   
10         M1P       Scarborough   
11         M1R       Scarborough   
11         M1R       Scarborough   
12         M1S       Scarborough   
13         M1T       Scarborough   
13         M1T       Scarborough   
13         M1T       Scarborough   
14         M1V       Scarborough   
14         M1V       Scarborough   
14         M1V       Scarborough   
14         M1V       Scarborough   
15         M1W       Scarborough   
16         M1X       Scarborough   
17         M2H        North York   
18         M2J        North York   
18         M2J        North York   
18         M2J        North York   
19         M2K        North York   
20         M2L        North York   
20         M2L        North York   
21         M2M        North York   
21         M2M        North York   
22         M2N        North York   
23         M2P        North York   
24         M2R        North York   
25         M3A        North York   
26         M3B        North York   
27         M3C        North York   
27         M3C        North York   
28         M3H        North York   
28         M3H        North York   
28         M3H        North York   
29         M3J        North York   
29         M3J        North York   
30         M3K        North York   
30         M3K        North York   
31         M3L        North York   
32         M3M        North York   
33         M3N        North York   
34         M4A        North York   
35         M4B         East York   
35         M4B         East York   
36         M4C         East York   
37         M4E      East Toronto   
38         M4G         East York   
39         M4H         East York   
40         M4J         East York   
41         M4K      East Toronto   
41         M4K      East Toronto   
42         M4L      East Toronto   
42         M4L      East Toronto   
43         M4M      East Toronto   
44         M4N   Central Toronto   
45         M4P   Central Toronto   
46         M4R   Central Toronto   
47         M4S   Central Toronto   
48         M4T   Central Toronto   
48         M4T   Central Toronto   
49         M4V   Central Toronto   
49         M4V   Central Toronto   
49         M4V   Central Toronto   
49         M4V   Central Toronto   
49         M4V   Central Toronto   
50         M4W  Downtown Toronto   
51         M4X  Downtown Toronto   
51         M4X  Downtown Toronto   
52         M4Y  Downtown Toronto   
53         M5A  Downtown Toronto   
54         M5B  Downtown Toronto   
54         M5B  Downtown Toronto   
55         M5C  Downtown Toronto   
56         M5E  Downtown Toronto   
57         M5G  Downtown Toronto   
58         M5H  Downtown Toronto   
58         M5H  Downtown Toronto   
58         M5H  Downtown Toronto   
59         M5J  Downtown Toronto   
59         M5J  Downtown Toronto   
59         M5J  Downtown Toronto   
60         M5K  Downtown Toronto   
60         M5K  Downtown Toronto   
61         M5L  Downtown Toronto   
61         M5L  Downtown Toronto   
62         M5M        North York   
62         M5M        North York   
63         M5N   Central Toronto   
64      

Finally, let's visualize the resulting clusters

### Lets remove entries with no data

In [43]:

toronto_merged = toronto_merged.dropna(subset=['Cluster Labels'])


In [44]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Latitude'], toronto_merged['Longitude'], toronto_merged['Neighborhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[(int)(cluster-1)],
        fill=True,
        fill_color=rainbow[(int)(cluster-1)],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

<a id='item5'></a>

## 5. Examine Clusters

Now, you can examine each cluster and determine the discriminating venue categories that distinguish each cluster. Based on the defining categories, you can then assign a name to each cluster. I will leave this exercise to you.

#### Cluster 1 "Family living" : lots of recreation areas but only few shops and places to eat & drink

In [45]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 0, toronto_merged.columns[[1,2] + list(range(5, toronto_merged.shape[1]))]]

Borough           Neighborhood  Cluster Labels  \
14        Scarborough               Milliken             0.0   
14        Scarborough           Steeles East             0.0   
14        Scarborough        L'Amoreaux East             0.0   
14        Scarborough        Agincourt North             0.0   
23         North York        York Mills West             0.0   
25         North York              Parkwoods             0.0   
30         North York            CFB Toronto             0.0   
30         North York         Downsview East             0.0   
40          East York           East Toronto             0.0   
44    Central Toronto          Lawrence Park             0.0   
48    Central Toronto        Summerhill East             0.0   
48    Central Toronto             Moore Park             0.0   
50   Downtown Toronto               Rosedale             0.0   
64    Central Toronto       Forest Hill West             0.0   
64    Central Toronto      Forest Hill North             0.0   
74               York    Caledonia-Fairbanks             0.0   
79         North York              Downsview             0.0   
79         North York             North Park             0.0   
79         North York            Upwood Park             0.0   
90          Etobicoke           The Kingsway             0.0   
90          Etobicoke         Old Mill North             0.0   
90          Etobicoke        Montgomery Road             0.0   
98               York                 Weston             0.0   
100         Etobicoke      Kingsview Village             0.0   
100         Etobicoke   Martin Grove Gardens             0.0   
100         Etobicoke           St. Phillips             0.0   
100         Etobicoke       Richview Gardens             0.0   

    1st Most Common Venue 2nd Most Common Venue       3rd Most Common Venue  \
14             Playground                  Park                 Coffee Shop   
14             Playground                  Park                 Coffee Shop   
14             Playground                  Park                 Coffee Shop   
14             Playground                  Park                 Coffee Shop   
23                   Park     Convenience Store                        Bank   
25                   Park     Food & Drink Shop  Construction & Landscaping   
30                   Park               Airport                           0   
30                   Park               Airport                           0   
40                   Park     Convenience Store                 Coffee Shop   
44            Swim School                  Park                    Bus Line   
48           Tennis Court            Restaurant                  Playground   
48           Tennis Court            Restaurant                  Playground   
50                   Park                 Trail                  Playground   
64                  Trail      Sushi Restaurant                        Park   
64                  Trail      Sushi Restaurant                        Park   
74                   Park         Women's Store                      Market   
79                   Park         Deli / Bodega  Construction & Landscaping   
79                   Park         Deli / Bodega  Construction & Landscaping   
79                   Park         Deli / Bodega  Construction & Landscaping   
90             Smoke Shop                 River                        Park   
90             Smoke Shop                 River                        Park   
90             Smoke Shop                 River                        Park   
98                   Park                     0                           0   
100           Pizza Place                  Park           Mobile Phone Shop   
100           Pizza Place                  Park           Mobile Phone Shop   
100           Pizza Place                  Park           Mobile Phone Shop   
100           Pizza Place                  Park           Mobile Phone Shop   

    4th 

#### Cluster 2 "Downtown" lots of different restaurants, shops & services

In [46]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 1, toronto_merged.columns[[1,2] + list(range(5, toronto_merged.shape[1]))]]

Borough                                       Neighborhood  \
0         Scarborough                                            Malvern   
0         Scarborough                                              Rouge   
2         Scarborough                                          West Hill   
2         Scarborough                                        Morningside   
2         Scarborough                                          Guildwood   
3         Scarborough                                             Woburn   
4         Scarborough                                          Cedarbrae   
5         Scarborough                                Scarborough Village   
6         Scarborough                               East Birchmount Park   
6         Scarborough                                       Kennedy Park   
6         Scarborough                                            Ionview   
7         Scarborough                                           Oakridge   
7         Scarborough                                           Clairlea   
7         Scarborough                                        Golden Mile   
8         Scarborough                                          Cliffside   
8         Scarborough                                         Cliffcrest   
8         Scarborough                           Scarborough Village West   
9         Scarborough                                     Cliffside West   
9         Scarborough                                        Birch Cliff   
10        Scarborough                            Scarborough Town Centre   
10        Scarborough                                    Wexford Heights   
10        Scarborough                                        Dorset Park   
11        Scarborough                                           Maryvale   
11        Scarborough                                            Wexford   
12        Scarborough                                          Agincourt   
13        Scarborough                                           Sullivan   
13        Scarborough                                      Tam O'Shanter   
13        Scarborough                                     Clarks Corners   
15        Scarborough                                    L'Amoreaux West   
17         North York                                  Hillcrest Village   
18         North York                                           Fairview   
18         North York                                         Henry Farm   
18         North York                                             Oriole   
19         North York                                    Bayview Village   
22         North York                                   Willowdale South   
24         North York                                    Willowdale West   
26         North York                                    Don Mills North   
27         North York                                    Don Mills South   
27         North York                                    Flemingdon Park   
28         North York                                     Bathurst Manor   
28         North York                                    Downsview North   
28         North York                                     Wilson Heights   
29         North York                                    York University   
29         North York                                     Northwood Park   
31         North York                                     Downsview West   
32         North York                                  Downsview Central   
33         North York                                Downsview Northwest   
34         North York                                   Victoria Village   
35          East York                                   Woodbine Gardens   
35          East York                                      Parkview Hill   
36          East York                                   Woodbine Heights   
37       East Toronto                                        T

#### Cluster 3 "Golf course" : no other infrastruture

In [47]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 2, toronto_merged.columns[[1,2] + list(range(5, toronto_merged.shape[1]))]]

Borough       Neighborhood  Cluster Labels 1st Most Common Venue  \
1   Scarborough     Highland Creek             2.0           Golf Course   
1   Scarborough         Port Union             2.0           Golf Course   
1   Scarborough         Rouge Hill             2.0           Golf Course   
94    Etobicoke         Cloverdale             2.0           Golf Course   
94    Etobicoke          Islington             2.0           Golf Course   
94    Etobicoke       Martin Grove             2.0           Golf Course   
94    Etobicoke   Princess Gardens             2.0           Golf Course   
94    Etobicoke    West Deane Park             2.0           Golf Course   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
1                    Bar                     0                     0   
1                    Bar                     0                     0   
1                    Bar                     0                     0   
94                     0                     0                     0   
94                     0                     0                     0   
94                     0                     0                     0   
94                     0                     0                     0   
94                     0                     0                     0   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
1                      0                     0                     0   
1                      0                     0                     0   
1                      0                     0                     0   
94                     0                     0                     0   
94                     0                     0                     0   
94                     0                     0                     0   
94                     0                     0                     0   
94                     0                     0                     0   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
1                      0                     0                      0  
1                      0                     0                      0  
1                      0                     0                      0  
94                     0                     0                      0  
94                     0                     0                      0  
94                     0                     0                      0  
94                     0                     0                      0  
94                     0                     0                      0

#### Cluster 4 "Baseball field"

In [48]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 3, toronto_merged.columns[[1,2] + list(range(5, toronto_merged.shape[1]))]]

Borough               Neighborhood  Cluster Labels  \
91   Etobicoke      Royal York South East             3.0   
91   Etobicoke                   Sunnylea             3.0   
91   Etobicoke         The Queensway East             3.0   
91   Etobicoke             Old Mill South             3.0   
91   Etobicoke   Kingsway Park South East             3.0   
91   Etobicoke           King's Mill Park             3.0   
91   Etobicoke                 Humber Bay             3.0   
91   Etobicoke                  Mimico NE             3.0   
97  North York                      Emery             3.0   
97  North York                  Humberlea             3.0   

   1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
91        Baseball Field                     0                     0   
91        Baseball Field                     0                     0   
91        Baseball Field                     0                     0   
91        Baseball Field                     0                     0   
91        Baseball Field                     0                     0   
91        Baseball Field                     0                     0   
91        Baseball Field                     0                     0   
91        Baseball Field                     0                     0   
97        Baseball Field                     0                     0   
97        Baseball Field                     0                     0   

   4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
91                     0                     0                     0   
91                     0                     0                     0   
91                     0                     0                     0   
91                     0                     0                     0   
91                     0                     0                     0   
91                     0                     0                     0   
91                     0                     0                     0   
91                     0                     0                     0   
97                     0                     0                     0   
97                     0                     0                     0   

   7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
91                     0                     0                     0   
91                     0                     0                     0   
91                     0                     0                     0   
91                     0                     0                     0   
91                     0                     0                     0   
91                     0                     0                     0   
91                     0                     0                     0   
91                     0                     0                     0   
97                     0                     0                     0   
97                     0                     0                     0   

   10th Most Common Venue  
91                      0  
91                      0  
91                      0  
91                      0  
91                      0  
91                      0  
91                      0  
91                      0  
97                      0  
97                      0

#### Cluster 5 "Cafeteria" no other infrastructure

In [49]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 4, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
20  North York             4.0             Cafeteria                     0   
20  North York             4.0             Cafeteria                     0   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
20                     0                     0                     0   
20                     0                     0                     0   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
20                     0                     0                     0   
20                     0                     0                     0   

   9th Most Common Venue 10th Most Common Venue  
20                     0                      0  
20                     0                      0